# **Installations**

In [ ]:

!pip install azure-storage-blob
!pip install google-cloud-storage

#need to update these packages to run the import codes

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 408.6/408.6 kB 8.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 198.9/198.9 kB 10.6 MB/s eta 0:00:00


# **Import Library**

In [ ]:
import requests
from requests.exceptions import RequestException
import json
import os
import time

In [ ]:
import pandas as pd
import numpy as np
from azure.storage.blob import BlobServiceClient, BlobClient, ContainerClient
import io

# **Codes for Data Extraction(WIP)**
- Below will be extracting the relevant data from dolthub:
  - **Time**: 2020-current
  - **States**: New York(NY), C
  - **County**
  - **Address & Zip**
  - **Sources**: Zillow & Redfin
  - **Sales Prices**


We want to extract data by chunks onto a single csv file in our Azure storage. The living wage JSON files provided by professor should be manually uploaded onto our cloud storage.
<br>The goal right now is to transform & clean data from dolthub and then merge them with living wage files based on location (county, state,zip...)

## UPLOADING BLOB

In [ ]:
#Uploading function definition
def google_upload_blob(bucket_name, source_file_name, destination_blob_name):
    storage_client = storage.Client()
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(destination_blob_name)
    blob.upload_from_filename(source_file_name)
    print(f"File {source_file_name} uploaded to {destination_blob_name}.")

## REQUESTING DATA

In [ ]:
owner = "dolthub"
database = "us-housing-prices-v2"  # Put the database
branch = "main"

#Microsoft Azure account information
Azure_Storage_Connection_String = "DefaultEndpointsProtocol=https;AccountName=housingproject;AccountKey=LOu0R1SQefZKhTKBLleRuVQ6ySFcGebQSXyzNDrnl2o7tpjZ+QWZxreXPDwJCPlDreFmVH0CZEKq+AStROgI1g==;EndpointSuffix=core.windows.net"
Container_Name = "housingdata"

In [ ]:
# Set the query to retrieve the data.
# This set of code spits back the total number of rows from our data source.
query = '''SELECT COUNT(*) FROM sales'''
res = requests.get(
  'https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch),
  params={'q': query},
  )

response = res.json()
total_count = int(response['rows'][0]['COUNT(*)'])
print(total_count)

106642382


In [ ]:
# Define the increment value
increment = 2500

# Starting offset
offset = 0

# Placeholder for the base SQL query
base_query = "SELECT * FROM sales WHERE state = 'NJ' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 2500 OFFSET {offset}"

# Loop through, updating the OFFSET each time
while offset < total_count:
    # Update the SQL query with the current offset
    updated_query = base_query.format(offset=offset)
    print(updated_query)

    # Retry logic
    retries = 6  # Number of retry attempts
    for i in range(retries):
        try:
            res = requests.get('https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch), params={'q': updated_query})
            res.raise_for_status()  # Raise an exception for bad status codes
            values = res.json()

            if "rows" in values:
                result = values['rows']
                print(result)
                break  # Exit the retry loop if successful

        except requests.exceptions.RequestException as e:
            print(f"Error during request (attempt {i + 1}/{retries}): {e}")
            if i < retries - 1:  # If it's not the last retry
                time.sleep(160)  # Wait for 20 min
                #12 min didn't work
                #15 min didn't work
            else:
                print("Max retries reached. Exiting.")
                break  # Exit the retry loop if max retries reached

    offset += increment

[{'state': 'PA', 'property_zip5': '34448', 'property_street_address': '0 (UNNAMED)', 'property_city': 'HOMOSASSA', 'property_county': 'CITRUS', 'property_id': '17E19S14      24000 0020', 'sale_datetime': '2020-03-17 00:00:00', 'property_type': None, 'sale_price': '100', 'seller_1_name': None, 'buyer_1_name': None, 'building_num_units': None, 'building_year_built': None, 'source_url': 'https://www.citruspa.org/_dnn/Downloads', 'book': '3047', 'page': '565', 'transfer_deed_type': None, 'property_township': None, 'property_lat': None, 'property_lon': None, 'sale_id': None, 'deed_date': None, 'building_num_stories': None, 'building_num_beds': None, 'building_num_baths': None, 'building_area_sqft': None, 'building_assessed_value': None, 'building_assessed_date': None, 'land_area_acres': None, 'land_area_sqft': None, 'land_assessed_value': None, 'seller_2_name': None, 'buyer_2_name': None, 'land_assessed_date': None, 'seller_1_state': None, 'seller_2_state': None, 'buyer_1_state': None, 'buy

KeyboardInterrupt: 

In [ ]:
total_count = int(response['rows'][0]['COUNT(*)'])
print(f"The number of rows is : {total_count}")

# Define the increment value
increment = 2500

# Starting offset - take note of what the offset was at for any point of error during request.
offset = 0

# Placeholder for the base SQL query, with an OFFSET placeholder
base_query = "SELECT * FROM sales WHERE state = 'NY' LIMIT 25000 OFFSET {offset}"

# Loop through, updating the OFFSET each time
while offset < total_count:
    # Update the SQL query with the current offset
    updated_query = base_query.format(offset=offset)
    print(updated_query)

    try:
        res = requests.get('https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch), params={'q': updated_query})
        res.raise_for_status()  # Raise an exception for bad status codes (like 504 - timeout due to excessive requests)
        values = res.json()

        if "rows" in values:
            result = values['rows']
            print(result)

    except requests.exceptions.RequestException as e:
        print(f"Error during request: {e}")
        # You might want to add retry logic here or break the loop
        break  # Break the loop to stop further requests

    offset += increment

The number of rows is : 106642382
SELECT * FROM sales WHERE state = 'NY' LIMIT 50000 OFFSET 0
[{'state': 'NY', 'property_zip5': '11795', 'property_street_address': '# 1299 MADISON AVE,', 'property_city': 'ISLIP', 'property_county': 'SUFFOLK', 'property_id': '362.-3-93', 'sale_datetime': '2017-05-30 00:00:00', 'property_type': 'ONE FAMILY YEAR-ROUND RESIDENCE', 'sale_price': '10000', 'seller_1_name': 'JOHN V. COPPOLA', 'buyer_1_name': 'TA CONSULTANTS GROUP INC.', 'building_num_units': None, 'building_year_built': None, 'source_url': 'https://swcf.orpts.ny.gov/cfapps/salesWebProd/salesWeb/main.cfm?page=downloadCounty', 'book': '12914', 'page': '965', 'transfer_deed_type': None, 'property_township': None, 'property_lat': None, 'property_lon': None, 'sale_id': None, 'deed_date': '2017-06-02 00:00:00', 'building_num_stories': None, 'building_num_beds': None, 'building_num_baths': None, 'building_area_sqft': None, 'building_assessed_value': None, 'building_assessed_date': '1970-01-01 00:00:0

KeyboardInterrupt: 

In [ ]:
# Define the increment value
increment = 2500

# Starting offset
offset = 0

# Placeholder for the base SQL query
base_query = "SELECT * FROM sales WHERE state = 'PA' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 2500 OFFSET {offset}"

# Loop through, updating the OFFSET each time
while offset < total_count:
    # Update the SQL query with the current offset
    updated_query = base_query.format(offset=offset)
    print(updated_query)

    # Retry logic
    retries = 6  # Number of retry attempts
    for i in range(retries):
        try:
            res = requests.get('https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch), params={'q': updated_query})
            res.raise_for_status()  # Raise an exception for bad status codes
            values = res.json()

            if "rows" in values:
                result = values['rows']
                print(result)
                break  # Exit the retry loop if successful

        except requests.exceptions.RequestException as e:
            print(f"Error during request (attempt {i + 1}/{retries}): {e}")
            if i < retries - 1:  # If it's not the last retry
                time.sleep(160)  # Wait for 20 min
                #12 min didn't work
                #15 min didn't work
            else:
                print("Max retries reached. Exiting.")
                break  # Exit the retry loop if max retries reached

    offset += increment

SELECT * FROM sales WHERE state = 'PA' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 2500 OFFSET 0
[{'state': 'PA', 'property_zip5': '34448', 'property_street_address': '0 (UNNAMED)', 'property_city': 'HOMOSASSA', 'property_county': 'CITRUS', 'property_id': '17E19S14      24000 0020', 'sale_datetime': '2020-03-17 00:00:00', 'property_type': None, 'sale_price': '100', 'seller_1_name': None, 'buyer_1_name': None, 'building_num_units': None, 'building_year_built': None, 'source_url': 'https://www.citruspa.org/_dnn/Downloads', 'book': '3047', 'page': '565', 'transfer_deed_type': None, 'property_township': None, 'property_lat': None, 'property_lon': None, 'sale_id': None, 'deed_date': None, 'building_num_stories': None, 'building_num_beds': None, 'building_num_baths': None, 'building_area_sqft': None, 'building_assessed_value': None, 'building_assessed_date': None, 'land_area_acres': None, 'land_area_sqft': None, 'land_assessed_value': None, 'seller_2_name': None, 'buyer_2_n

KeyboardInterrupt: 

# **Codes for Data Reformatting/Transforming/Cleaning**
Extract and upload data onto our cloud storage first. Then we can call them from storage and transform/clean via scripts here.
(Did not end up using this or exploring any more since we have DBT to building and transform our data - Willy)

In [ ]:
result

[{'state': 'PA',
  'property_zip5': '15206',
  'property_street_address': '0 S NEGLEY AVE',
  'property_city': 'PITTSBURGH',
  'property_county': 'ALLEGHENY',
  'property_id': '0084A00062000000',
  'sale_datetime': '2021-02-05 00:00:00',
  'property_type': None,
  'sale_price': '1049000',
  'seller_1_name': None,
  'buyer_1_name': None,
  'building_num_units': None,
  'building_year_built': None,
  'source_url': 'https://data.wprdc.org/dataset/real-estate-sales',
  'book': '18328',
  'page': '416',
  'transfer_deed_type': None,
  'property_township': None,
  'property_lat': None,
  'property_lon': None,
  'sale_id': None,
  'deed_date': None,
  'building_num_stories': None,
  'building_num_beds': None,
  'building_num_baths': None,
  'building_area_sqft': None,
  'building_assessed_value': None,
  'building_assessed_date': None,
  'land_area_acres': None,
  'land_area_sqft': None,
  'land_assessed_value': None,
  'seller_2_name': None,
  'buyer_2_name': None,
  'land_assessed_date': No

# Testing Code from Google Gemini with limit of 50,000 and offsets require to complete through the total rows


# NJ

In [ ]:
owner = "dolthub"
database = "us-housing-prices-v2"  # Put the database
branch = "main"

#Microsoft Azure account information
Azure_Storage_Connection_String = "DefaultEndpointsProtocol=https;AccountName=housingproject;AccountKey=LOu0R1SQefZKhTKBLleRuVQ6ySFcGebQSXyzNDrnl2o7tpjZ+QWZxreXPDwJCPlDreFmVH0CZEKq+AStROgI1g==;EndpointSuffix=core.windows.net"
Container_Name = "housingdata"

In [ ]:
# Set the query to retrieve the data.
# This set of code spits back the total number of rows from our data source.
query = '''SELECT COUNT(*) FROM sales'''
res = requests.get(
  'https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch),
  params={'q': query},
  )

response = res.json()
total_count = int(response['rows'][0]['COUNT(*)'])
print(total_count)

106642382


In [ ]:
def upload_to_azure_nj(df, offset):
    """Uploads a Pandas DataFrame to Azure Blob Storage.

    Args:
        df: The Pandas DataFrame to upload.
        offset: The current offset in the data retrieval.
    """
    # Create a BlobServiceClient using your connection string
    blob_service_client = BlobServiceClient.from_connection_string(Azure_Storage_Connection_String)

    # Get a BlobClient for the desired blob
    blob_client = blob_service_client.get_blob_client(container=Container_Name, blob=f"nj_data_chunk_{offset}.csv")

    # Convert the DataFrame to CSV data in memory
    csv_data = df.to_csv(index=False).encode('utf-8')

    # Upload the CSV data to Azure Blob Storage
    blob_client.upload_blob(csv_data, overwrite=True)

    print(f"Uploaded data chunk with offset {offset} to Azure Blob Storage.")

In [ ]:
total_count = int(response['rows'][0]['COUNT(*)'])
print(f"The number of rows is : {total_count}")

# Define the increment value (maximum allowed per request)
increment = 1000

# Starting offset
offset = 0

# Set the time delay
time_nj = 5

base_query = "SELECT * FROM sales WHERE state = 'NJ' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT {limit} OFFSET {offset}"

while True:  # Loop indefinitely until a break condition is met
    # Update the SQL query with the current offset and limit
    updated_query = base_query.format(limit=increment, offset=offset)
    print(updated_query)

    try:
       res = requests.get('https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch), params={'q': updated_query})
       res.raise_for_status()
       values = res.json()

       if "rows" in values:
           result = values['rows']
           df = pd.DataFrame(result)
           upload_to_azure_nj(df, offset)
           time.sleep(30)
    except requests.exceptions.RequestException as e:
       print(f"Error during request: {e}")
       print(f"Retrying in {time_nj} seconds...")
       time.sleep(time_nj)
       continue

    offset += increment

The number of rows is : 106642382
SELECT * FROM sales WHERE state = 'NJ' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 1000 OFFSET 0
Uploaded data chunk with offset 0 to Azure Blob Storage.
SELECT * FROM sales WHERE state = 'NJ' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 1000 OFFSET 1000
Uploaded data chunk with offset 1000 to Azure Blob Storage.
SELECT * FROM sales WHERE state = 'NJ' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 1000 OFFSET 2000
Uploaded data chunk with offset 2000 to Azure Blob Storage.
SELECT * FROM sales WHERE state = 'NJ' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 1000 OFFSET 3000
Uploaded data chunk with offset 3000 to Azure Blob Storage.
SELECT * FROM sales WHERE state = 'NJ' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 1000 OFFSET 4000
Uploaded data chunk with offset 4000 to Azure Blob Storage.
SELECT * FROM sales WHERE state = 'NJ' AND sale_datetime BETWEEN '2019-01-01' AND 

In [ ]:
import requests
import time
import pandas as pd

# Repository details
owner = 'dolthub'
database = 'us-housing-prices-v2'
branch = 'main'

# Get total count first
count_query = "SELECT COUNT(*) FROM sales WHERE state = 'CT'"
res = requests.get(
    f'https://www.dolthub.com/api/v1alpha1/{owner}/{database}/{branch}',
    params={'q': count_query}
)
response = res.json()

total_count = int(response['rows'][0]['COUNT(*)'])
print(f"The number of rows is : {total_count}")

# Define the increment value (maximum allowed per request)
increment = 2500

# Starting offset
offset = 0  # Start from beginning for CT

# Set the time delay
time_ct = 10

# Base query for Connecticut
base_query = "SELECT * FROM sales WHERE state = 'CT' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT {limit} OFFSET {offset}"

print("Sample query that will be used:", base_query.format(limit=increment, offset=0))
print("\
Total count:", total_count)
print("Increment size:", increment)
print("Starting offset:", offset)

JSONDecodeError: Expecting value: line 1 column 1 (char 0)


# NY

In [ ]:
def upload_to_azure_ny(df, offset):
    """Uploads a Pandas DataFrame to Azure Blob Storage.

    Args:
        df: The Pandas DataFrame to upload.
        offset: The current offset in the data retrieval.
    """
    # Create a BlobServiceClient using your connection string
    blob_service_client = BlobServiceClient.from_connection_string(Azure_Storage_Connection_String)

    # Get a BlobClient for the desired blob
    blob_client = blob_service_client.get_blob_client(container=Container_Name, blob=f"ny_data_chunk_{offset}.csv")

    # Convert the DataFrame to CSV data in memory
    csv_data = df.to_csv(index=False).encode('utf-8')

    # Upload the CSV data to Azure Blob Storage
    blob_client.upload_blob(csv_data, overwrite=True)

    print(f"Uploaded data chunk with offset {offset} to Azure Blob Storage.")

In [ ]:
total_count = int(response['rows'][0]['COUNT(*)'])
print(f"The number of rows is : {total_count}")

# Define the increment value (maximum allowed per request)
increment = 1000

# Starting offset
offset = 0

# Set the time delay
time_nj = 5

base_query = "SELECT * FROM sales WHERE state = 'NY' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT {limit} OFFSET {offset}"

while True:  # Loop indefinitely until a break condition is met
    # Update the SQL query with the current offset and limit
    updated_query = base_query.format(limit=increment, offset=offset)
    print(updated_query)

    try:
       res = requests.get('https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch), params={'q': updated_query})
       res.raise_for_status()
       values = res.json()

       if "rows" in values:
           result = values['rows']
           df = pd.DataFrame(result)
           upload_to_azure_ny(df, offset)
           time.sleep(30)
    except requests.exceptions.RequestException as e:
       print(f"Error during request: {e}")
       print(f"Retrying in {time_nj} seconds...")
       time.sleep(time_nj)
       continue

    offset += increment

# PA

In [ ]:
owner = "dolthub"
database = "us-housing-prices-v2"  # Put the database
branch = "main"

#Microsoft Azure account information
Azure_Storage_Connection_String = "DefaultEndpointsProtocol=https;AccountName=housingproject;AccountKey=LOu0R1SQefZKhTKBLleRuVQ6ySFcGebQSXyzNDrnl2o7tpjZ+QWZxreXPDwJCPlDreFmVH0CZEKq+AStROgI1g==;EndpointSuffix=core.windows.net"
Container_Name = "housingdata"

# Set the query to retrieve the data.
# This set of code spits back the total number of rows from our data source.
query = '''SELECT COUNT(*) FROM sales'''
res = requests.get(
  'https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch),
  params={'q': query},
  )

response = res.json()
total_count = int(response['rows'][0]['COUNT(*)'])
print(total_count)

106642382


In [ ]:
def upload_to_azure_pa(df, offset):
    """Uploads a Pandas DataFrame to Azure Blob Storage.

    Args:
        df: The Pandas DataFrame to upload.
        offset: The current offset in the data retrieval.
    """
    # Create a BlobServiceClient using your connection string
    blob_service_client = BlobServiceClient.from_connection_string(Azure_Storage_Connection_String)

    # Get a BlobClient for the desired blob
    blob_client = blob_service_client.get_blob_client(container=Container_Name, blob=f"pa_data_chunk_{offset}.csv")

    # Convert the DataFrame to CSV data in memory
    csv_data = df.to_csv(index=False).encode('utf-8')

    # Upload the CSV data to Azure Blob Storage
    blob_client.upload_blob(csv_data, overwrite=True)

    print(f"Uploaded data chunk with offset {offset} to Azure Blob Storage.")


total_count = int(response['rows'][0]['COUNT(*)'])
print(f"The number of rows is : {total_count}")

# Define the increment value (maximum allowed per request)
increment = 1000

# Starting offset
offset = 0

# Set the time delay
time_retry = 5

base_query = "SELECT * FROM sales WHERE state = 'PA' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT {limit} OFFSET {offset}"

while True:  # Loop indefinitely until a break condition is met
    # Update the SQL query with the current offset and limit
    updated_query = base_query.format(limit=increment, offset=offset)
    print(updated_query)

    try:
       res = requests.get('https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch), params={'q': updated_query})
       res.raise_for_status()
       values = res.json()

       if "rows" in values:
           result = values['rows']
           df = pd.DataFrame(result)
           upload_to_azure_pa(df, offset)
           time.sleep(30)
    except requests.exceptions.RequestException as e:
       print(f"Error during request: {e}")
       print(f"Retrying in {time_retry} seconds...")
       time.sleep(time_retry)
       continue

    offset += increment


The number of rows is : 106642382
SELECT * FROM sales WHERE state = 'PA' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 1000 OFFSET 0
Uploaded data chunk with offset 0 to Azure Blob Storage.
SELECT * FROM sales WHERE state = 'PA' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 1000 OFFSET 1000
Uploaded data chunk with offset 1000 to Azure Blob Storage.
SELECT * FROM sales WHERE state = 'PA' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 1000 OFFSET 2000
Uploaded data chunk with offset 2000 to Azure Blob Storage.
SELECT * FROM sales WHERE state = 'PA' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 1000 OFFSET 3000
Uploaded data chunk with offset 3000 to Azure Blob Storage.
SELECT * FROM sales WHERE state = 'PA' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT 1000 OFFSET 4000
Uploaded data chunk with offset 4000 to Azure Blob Storage.
SELECT * FROM sales WHERE state = 'PA' AND sale_datetime BETWEEN '2019-01-01' AND 

# CT

In [ ]:
owner = "dolthub"
database = "us-housing-prices-v2"  # Put the database
branch = "main"

#Microsoft Azure account information
Azure_Storage_Connection_String = "DefaultEndpointsProtocol=https;AccountName=housingproject;AccountKey=LOu0R1SQefZKhTKBLleRuVQ6ySFcGebQSXyzNDrnl2o7tpjZ+QWZxreXPDwJCPlDreFmVH0CZEKq+AStROgI1g==;EndpointSuffix=core.windows.net"
Container_Name = "housingdata"

# Set the query to retrieve the data.
# This set of code spits back the total number of rows from our data source.
query = '''SELECT COUNT(*) FROM sales'''
res = requests.get(
  'https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch),
  params={'q': query},
  )

response = res.json()
total_count = int(response['rows'][0]['COUNT(*)'])
print(total_count)

In [ ]:
def upload_to_azure_ct(df, offset):
    """Uploads a Pandas DataFrame to Azure Blob Storage.

    Args:
        df: The Pandas DataFrame to upload.
        offset: The current offset in the data retrieval.
    """
    # Create a BlobServiceClient using your connection string
    blob_service_client = BlobServiceClient.from_connection_string(Azure_Storage_Connection_String)

    # Get a BlobClient for the desired blob
    blob_client = blob_service_client.get_blob_client(container=Container_Name, blob=f"ct_data_chunk_{offset}.csv")

    # Convert the DataFrame to CSV data in memory
    csv_data = df.to_csv(index=False).encode('utf-8')

    # Upload the CSV data to Azure Blob Storage
    blob_client.upload_blob(csv_data, overwrite=True)

    print(f"Uploaded data chunk with offset {offset} to Azure Blob Storage.")


total_count = int(response['rows'][0]['COUNT(*)'])
print(f"The number of rows is : {total_count}")

# Define the increment value (maximum allowed per request)
increment = 1000

# Starting offset
offset = 0

# Set the time delay
time_retry = 5

base_query = "SELECT * FROM sales WHERE state = 'CT' AND sale_datetime BETWEEN '2019-01-01' AND '2023-12-30' LIMIT {limit} OFFSET {offset}"

while True:  # Loop indefinitely until a break condition is met
    # Update the SQL query with the current offset and limit
    updated_query = base_query.format(limit=increment, offset=offset)
    print(updated_query)

    try:
       res = requests.get('https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch), params={'q': updated_query})
       res.raise_for_status()
       values = res.json()

       if "rows" in values:
           result = values['rows']
           df = pd.DataFrame(result)
           upload_to_azure_ct(df, offset)
           time.sleep(30)
    except requests.exceptions.RequestException as e:
       print(f"Error during request: {e}")
       print(f"Retrying in {time_retry} seconds...")
       time.sleep(time_retry)
       continue

    offset += increment
